In [4]:
from string import punctuation
from os import listdir
from numpy import array
from numpy import asarray
from numpy import zeros
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers import Embedding
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D

#from string import punctuation
#from os import listdir
from collections import Counter
from nltk.corpus import stopwords

import fileRetriever

# load doc into memory
def load_doc(filename):
	# open the file as read only
	file = open(filename, 'r')
	# read all text
	text = file.read()
	# close the file
	file.close()
	return text

# turn a doc into clean tokens
def clean_doc(doc, vocab):
	# split into tokens by white space
	tokens = doc.split()
	# remove punctuation from each token
	table = str.maketrans('', '', punctuation)
	tokens = [w.translate(table) for w in tokens]
	# filter out tokens not in vocab
	tokens = [w for w in tokens if w in vocab]
	tokens = ' '.join(tokens)
	return tokens

# load doc and add to vocab
def add_doc_to_vocab(filename, vocab):
	# load doc
	doc = load_doc(filename)
	# clean doc
	tokens = clean_doc(doc)
	# update counts
	vocab.update(tokens)

# load all docs in a directory
def process_docs(directory, vocab, is_trian):
    documents = list()
    # walk through all files in the folder
    for filename in listdir(directory):
        # skip any reviews in the test set
        if fileRetriever.hasCorrectExtension(filename):
            # create the full path of the file to open
            path = directory + '/' + filename
            # load the doc
            doc = load_doc(path)
            # clean doc
            tokens = clean_doc(doc, vocab)
            # add to list
            documents.append(tokens)
            
            # add doc to vocab
            add_doc_to_vocab(path, vocab)
    return documents

# save list to file
def save_list(lines, filename):
	# convert lines to a single blob of text
	data = '\n'.join(lines)
	# open file
	file = open(filename, 'w')
	# write text
	file.write(data)
	# close file
	file.close()

# load embedding as a dict
def load_embedding(filename):
	# load embedding into memory, skip first line
	file = open(filename,'r')
	lines = file.readlines()
	file.close()
	# create a map of words to vectors
	embedding = dict()
	for line in lines:
		parts = line.split()
		# key is string word, value is numpy array for vector
		embedding[parts[0]] = asarray(parts[1:], dtype='float32')
	return embedding

# create a weight matrix for the Embedding layer from a loaded embedding
def get_weight_matrix(embedding, vocab):
	# total vocabulary size plus 0 for unknown words
	vocab_size = len(vocab) + 1
	# define weight matrix dimensions with all 0
	weight_matrix = zeros((vocab_size, 100))
	# step vocab, store vectors using the Tokenizer's integer mapping
	for word, i in vocab.items():
		vector = embedding.get(word)
		if vector is not None:
			weight_matrix[i] = vector
	return weight_matrix

#vulner/nonvulner directories
nonvulnerDir = "../FullFileSet/Nonvulnerable"
vulnerDir = "../FullFileSet/Vulnerable"

# define vocab
vocab = Counter()
# add all docs to vocab
process_docs(nonvulnerDir, vocab, True) #process_docs('txt_sentoken/neg', vocab, True)
process_docs(vulnerDir, vocab, True) #process_docs('txt_sentoken/pos', vocab, True)
# print the size of the vocab
print(len(vocab))
# print the top words in the vocab
print(vocab.most_common(50))

# keep tokens with a min occurrence
min_occurane = 2
tokens = [k for k,c in vocab.items() if c >= min_occurane]
print(len(tokens))
# save tokens to a vocabulary file
save_list(tokens, 'vocab.txt')

# load the vocabulary
vocab_filename = 'vocab.txt'
vocab = load_doc(vocab_filename)
vocab = vocab.split()
vocab = set(vocab)

# load all training reviews
positive_docs = process_docs(vulnerDir, vocab, True) #positive_docs = process_docs('txt_sentoken/pos', vocab, True)
negative_docs = process_docs(nonvulnerDir, vocab, True) #negative_docs = process_docs('txt_sentoken/neg', vocab, True)
train_docs = negative_docs + positive_docs

# create the tokenizer
tokenizer = Tokenizer()
# fit the tokenizer on the documents
tokenizer.fit_on_texts(train_docs)

# sequence encode
encoded_docs = tokenizer.texts_to_sequences(train_docs)
# pad sequences
max_length = max([len(s.split()) for s in train_docs])
Xtrain = pad_sequences(encoded_docs, maxlen=max_length, padding='post')
# define training labels
ytrain = array([0 for _ in range(900)] + [1 for _ in range(900)])

# load all test reviews
positive_docs = process_docs('txt_sentoken/pos', vocab, False)
negative_docs = process_docs('txt_sentoken/neg', vocab, False)
test_docs = negative_docs + positive_docs
# sequence encode
encoded_docs = tokenizer.texts_to_sequences(test_docs)
# pad sequences
Xtest = pad_sequences(encoded_docs, maxlen=max_length, padding='post')
# define test labels
ytest = array([0 for _ in range(100)] + [1 for _ in range(100)])

# define vocabulary size (largest integer value)
vocab_size = len(tokenizer.word_index) + 1

# load embedding from file
raw_embedding = load_embedding('glove.6B.100d.txt')
# get vectors in the right order
embedding_vectors = get_weight_matrix(raw_embedding, tokenizer.word_index)
# create the embedding layer
embedding_layer = Embedding(vocab_size, 100, weights=[embedding_vectors], input_length=max_length, trainable=False)

# define model
model = Sequential()
model.add(embedding_layer)
model.add(Conv1D(filters=128, kernel_size=5, activation='relu'))
model.add(MaxPooling1D(pool_size=2))
model.add(Flatten())
model.add(Dense(1, activation='sigmoid'))
print(model.summary())
# compile network
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit network
model.fit(Xtrain, ytrain, epochs=10, verbose=2)
# evaluate
loss, acc = model.evaluate(Xtest, ytest, verbose=0)
print('Test Accuracy: %f' % (acc*100))

TypeError: clean_doc() missing 1 required positional argument: 'vocab'

In [9]:
from string import punctuation
from os import listdir
from collections import Counter
from nltk.corpus import stopwords

import fileRetriever
import os

# load doc into memory
def load_doc(filename):
	# open the file as read only
	file = open(filename, 'r')
	# read all text
	text = file.read()
	# close the file
	file.close()
	return text

# turn a doc into clean tokens
def clean_doc(doc):
	# split into tokens by white space
	tokens = doc.split()
	# remove punctuation from each token
	table = str.maketrans('', '', punctuation)
	tokens = [w.translate(table) for w in tokens]
	# remove remaining tokens that are not alphabetic
	tokens = [word for word in tokens if word.isalpha()]
	# filter out stop words
	stop_words = set(stopwords.words('english'))
	tokens = [w for w in tokens if not w in stop_words]
	# filter out short tokens
	tokens = [word for word in tokens if len(word) > 1]
	return tokens

# load doc and add to vocab
def add_doc_to_vocab(filename, vocab):
	# load doc
	doc = load_doc(filename)
	# clean doc
	tokens = clean_doc(doc)
	# update counts
	vocab.update(tokens)

# load all docs in a directory
'''def process_docs(directory, vocab, is_trian):
	# walk through all files in the folder
	for filename in listdir(directory):
		# skip any reviews in the test set
		if is_trian and filename.startswith('cv9'):
			continue
		if not is_trian and not filename.startswith('cv9'):
			continue
		# create the full path of the file to open
		path = directory + '/' + filename
		# add doc to vocab
		add_doc_to_vocab(path, vocab)'''

def process_docs(directory, vocab, is_trian):
    # walk through all files in the folder
    #parse through FileSet
    fileList = []
    for root, dirs, files in os.walk(directory):
        for name in files:
            currentFile = os.path.join(root, name)
            print(currentFile)
            if fileRetriever.hasCorrectExtension(currentFile):
                fileList.append(currentFile)
    return fileList


#vulner/nonvulner directories
nonvulnerDir = os.path.join("..", "FullFileSet", "Nonvulnerable")
vulnerDir = os.path.join("..", "FullFileSet", "Vulnerable")
        
# define vocab
vocab = Counter()
# add all docs to vocab
process_docs(nonvulnerDir, vocab, True)
process_docs(vulnerDir, vocab, True)
# print the size of the vocab
print(len(vocab))
# print the top words in the vocab
print(vocab.most_common(50))

..\FullFileSet\Nonvulnerable\class-bulk-editor-list-table.php
..\FullFileSet\Nonvulnerable\class-wp-query.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-concatenation.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-interpretation.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-sprintf_%d.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-sprintf_%d_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__array-GET__CAST-cast_float_sort_of__multiple_AS-sprintf_%u.php
..\FullFileSet\Nonvulner

..\FullFileSet\Nonvulnerable\CWE_89__GET__func_mysql_real_escape_string__select_from_where-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_mysql_real_escape_string__select_from_where-sprintf_%u.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_mysql_real_escape_string__select_from_where-sprintf_%u_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__join-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__join-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__join-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__select_from-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__select_from-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__GET__func_preg_match-letters_numbers__select_from-s

..\FullFileSet\Nonvulnerable\CWE_89__popen__func_addslashes__select_from-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_addslashes__select_from-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_addslashes__select_from-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-magic_quotes_filter__join-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-magic_quotes_filter__join-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-magic_quotes_filter__join-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-magic_quotes_filter__select_from-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-magic_quotes_filter__select_from-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__popen__func_FILTER-CLEANING-ma

..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-concatenation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-interpretation.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-interpretation_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-sprintf_%d.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-sprintf_%d_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-sprintf_%s_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-sprintf_%u.php
..\FullFileSet\Nonvulnerable\CWE_89__shell_exec__whitelist_using_array__select_from_where-sprintf_%u_simple_quote.php
..\FullFileSet\Nonvulnerable\CWE_89__system__CAST-cast_float_sort_of__multiple_AS-co

..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\ArchiveManager.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\ArchiverInterface.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\BaseExcludeFilter.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\ComposerExcludeFilter.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\GitExcludeFilter.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\HgExcludeFilter.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\PharArchiver.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Archiver\ZipArchiver.php
..\FullFileSet\Nonvulnerable\composer-master\composer-master\src\Composer\Package\Comparer\Comparer.php
..\Fu

...

..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Block\Adminhtml\Rate\ImportExportTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Controller\Adminhtml\Rate\ExportPostTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Controller\Adminhtml\Rate\ImportExportTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Controller\Adminhtml\Rate\ImportPostTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Model\Rate\CsvImportHandlerTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\dev\tests\integration\testsuite\Magento\TaxImportExport\Model\Rate\_files\corre

..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Asset\MaterializationStrategy\Copy.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Asset\MaterializationStrategy\Factory.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Asset\MaterializationStrategy\StrategyInterface.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Asset\MaterializationStrategy\Symlink.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Deployment\Version.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\App\View\Deployment\Version\StorageInterface.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Fram

..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\Request\Aggregation\StatusTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\Request\Config\SchemaLocatorTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\Response\AggregationTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\Response\QueryResponseTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\SearchEngine\Config\ConverterTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\internal\Magento\Framework\Search\Test\Unit\SearchEngine\Config\SchemaLocatorTest.php
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib

..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\save\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\searchreplace\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\spellchecker\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\tabfocus\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\table\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\template\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\textcolor\plugin.min.js
..\FullFileSet\Nonvulnerable\magento2-2.3-develop\magento2-2.3-develop\lib\web\tiny_mce_4\plugins\textpattern\plugin.min.js
..\FullFileSet\Nonvulnerab

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

